In [0]:
%run "./ADLS Setup Variables_SP"

In [0]:
from pyspark.sql.functions import when, from_json, col, explode, lit, udf, split, count, size, element_at, hour, day, weekofyear, month, year, date_format, count, avg, sum
from pyspark.sql.types import IntegerType
import pyspark.sql.functions as F
import pandas as pd
import matplotlib.pyplot as plt
import os


## Loading in the gold layer

In [0]:
org_dim = spark.read.format('parquet').load(gold_path + "OrgDim")
repo_dim = spark.read.format('parquet').load(gold_path + "RepoDim")
actor_dim = spark.read.format('parquet').load(gold_path + "ActorDim")
event_fact = spark.read.format('parquet').load(gold_path + "EventFact")
event_dim = spark.read.format('parquet').load(gold_path + "EventDim")
pe_dim = spark.read.format('parquet').load(gold_path + "PushEventDim")
# commit_dim = spark.read.format('parquet').load(gold_path + "CommitDim")

# Use Case 1 : Data aggregated by type of GitHub event per hour 


In [0]:
event_dim = event_dim.withColumn("hour", hour(col("created_at")))

In [0]:
hourly_events = event_dim.groupBy("type","hour").agg(count("type").alias("count"))

In [0]:
# count of each event that occurred per hour 
hourly_events.display()

In [0]:
tot_event_perhr = hourly_events.groupBy('hour').agg(sum('count').alias('count'))

In [0]:
def display_type(type:str):
    display(hourly_events.filter(col('type') == type))

In [0]:
def display_hour(hour:int):
    if (hour <= 23) or (hour >= 0): 
        display(hourly_events.filter(col('hour') == hour))

In [0]:
events = ['CommitCommentEvent','CreateEvent','DeleteEvent','ForkEvent','GollumEvent','IssueCommentEvent','IssuesEvent','MemberEvent','PublicEvent','PullRequestEvent','PullRequestReviewCommentEvent','PullRequestReviewEvent','PushEvent','ReleaseEvent','WatchEvent']
i = 0
display_type(events[i])

In [0]:
hour = 0   
display_hour(hour)

# Use Case 2 : PushEvent data aggregated by ref type – whether the commit is on the main branch 


In [0]:
pe_dim = pe_dim.withColumn("is_main",
    when(col("ref").endswith("main"), "True")
    .when(col("ref").endswith("master"), "True")
    .otherwise("False"))

In [0]:
display(pe_dim)

id ref is_main 8851714666 refs/heads/main True 8944668089 refs/heads/feature/dockerize-build-scripts False 8789450881 refs/heads/master True 8826682994 refs/heads/fix False 8839591321 refs/heads/master True 8783909128 refs/heads/main True 8765936045 refs/heads/master True 8818548334 refs/heads/master True 8776986836 refs/heads/feed False 8918175405 refs/heads/master True 8861772523 refs/heads/master True 8901539599 refs/heads/main True 8846570789 refs/heads/main True 8866948082 refs/heads/octaviusColorLetterContactBackgroundAlpha2 False 8762578197 refs/heads/main True 8766292650 refs/heads/main True 8820198284 refs/heads/master True 8806084387 refs/heads/master True 8813489365 refs/heads/master True 8861939130 refs/heads/master True 8800577848 refs/heads/main True 8812485031 refs/heads/main True 8794962842 refs/heads/main True 8843946450 refs/heads/master True 8742673437 refs/heads/output False 8772337485 refs/heads/master True 8844705115 refs/heads/main True 8807078911 refs/heads/master True 8749808033 refs/heads/main True 8784897519 refs/heads/master True 8733203092 refs/heads/main True 8889764415 refs/heads/main True 8900394372 refs/heads/dev False 8758230930 refs/heads/main True 8947222501 refs/heads/master True 8890074032 refs/heads/main True 8944115305 refs/heads/master True 8910514191 refs/heads/main True 8906022671 refs/heads/master True 8842391399 refs/heads/main True 8766117712 refs/heads/main True 8771875258 refs/heads/mamdfgdsfgdfg False 8902942701 refs/heads/main True 8949701190 refs/heads/main True 8902206879 refs/heads/yate False 8787657983 refs/heads/master True 8881194078 refs/heads/master True 8761153779 refs/heads/main True 8897874729 refs/heads/gh-pages False 8904830283 refs/heads/main True 8761575245 refs/heads/master True 8820261763 refs/heads/main True 8880446898 refs/heads/master True 8765355296 refs/heads/master True 8789692435 refs/heads/main True 8754687641 refs/heads/master True 8761596825 refs/heads/main True 8942541894 refs/heads/main True 8795907705 refs/heads/components-reorder False 8867631172 refs/heads/SolarStorm False 8920968567 refs/heads/early-2022-update False 8953836370 refs/heads/master True 8738791476 refs/heads/master True 8890257647 refs/heads/output False 8829063946 refs/heads/development False 8893592960 refs/heads/main True 8738141418 refs/heads/master True 8813406394 refs/heads/main True 8840913195 refs/heads/1.13 False 8874768384 refs/heads/main True 8965179133 refs/heads/main True 8920509339 refs/heads/main True 8905299384 refs/heads/feed False 8750806080 refs/heads/master True 8851678326 refs/heads/main True 8860779374 refs/heads/testing False 8741882118 refs/heads/master True 8856067986 refs/heads/main True 8753499210 refs/heads/PP-108/collector-contract False 8859300517 refs/heads/master True 8967549874 refs/heads/master True 8902552322 refs/heads/main True 8783872109 refs/heads/master True 8865244163 refs/heads/main True 8864781142 refs/heads/main True 8741332001 refs/heads/dev False 8742133083 refs/heads/main True 8765915777 refs/heads/github_actions False 8732426425 refs/heads/main True 8935003318 refs/heads/Master False 8780777038 refs/heads/main True 8773937378 refs/heads/master True 8765112989 refs/heads/master True 8888273191 refs/heads/main True 8759908010 refs/heads/master True 8742647483 refs/heads/main True 8737586746 refs/heads/main True 8793481195 refs/heads/master True 8802866476 refs/heads/master True 8857765605 refs/heads/master True 8747665357 refs/heads/master True 8972486261 refs/heads/home_screen False 8886530208 refs/heads/ui False 8970179262 refs/heads/dev False 8746841983 refs/heads/main True 8820673281 refs/heads/master True 8977468765 refs/heads/main True 8779090503 refs/heads/main True 8860021519 refs/heads/master True 8753545093 refs/heads/master True 8741057843 refs/heads/master True 8845845036 refs/heads/gh-pages False 8735060131 refs/heads/master True 8803098087 refs/heads/witness_mhutchinson_witness_Pixel-Transparency-Log-2021 False 8892533823 

In [0]:
main_branch = pe_dim.groupBy("is_main").agg(count("is_main").alias("count"))

In [0]:
display(main_branch)

In [0]:
branch_heat = pe_dim.groupBy('ref').agg(count('ref').alias('count'))

In [0]:
display(branch_heat)

In [0]:
def pop_repos():
    fact = (event_fact
            .join(repo_dim, repo_dim.id == event_fact.repo_id)
    )
    display(fact)
    """
    (fact
     .join(repo_dim, repo_dim["id"] == fact["repo_id"])
     .na.drop(subset=["repo_id"])
     .select('name','url',)
     ).display()
     """

In [0]:
pop_repos()

id actor_id repo_id org_id event_id push_id pe_size pe_distinct_size commit_id id name url 19806096608 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19806376761 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19809537308 1915363 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19806223834 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19785723327 61327399 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19806338017 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19806193400 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19806093999 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19806285867 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19794835698 61327399 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19986652414 98160327 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19912169290 95429420 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19806473190 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19808645188 1915363 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19806330680 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19806195452 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19806275355 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19829748018 61327399 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19817269462 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19808762788 1915363 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19817684503 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19808764825 1915363 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19806222083 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19806193832 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19817683820 57764042 26 null null null null null null 26 wycats/merb-core https://api.github.com/repos/wycats/merb-core 19872437210 57764042 29 null null null null null null 29 vanpelt/jsawesome https://api.github.com/repos/vanpelt/jsawesome 19872413357 57764042 29 null null null null null null 29 vanpelt/jsawesome https://api.github.com/repos/vanpelt/jsawesome 19817057167 57764042 29 null null null null null null 29 vanpelt/jsawesome https://api.github.com/repos/vanpelt/jsawesome 19809616169 1915363 29 null null null null null null 29 vanpelt/jsawesome https://api.github.com/repos/vanpelt/jsawesome 19927038340 1915363 29 null null null null null null 29 vanpelt/jsawesome https://api.github.com/repos/vanpelt/jsawesome 19855133056 57764042 29 null null null null null null 29 vanpelt/jsawesome https://api.github.com/repos/vanpelt/jsawesome 19680236821 95429420 29 null null null null null null 29 vanpelt/jsawesome https://api.github.com/repos/vanpelt/jsawesome 19984542409 98160327 29 null null null null null null 29 vanp

In [0]:
# Extract data for the chart
# labels = ['True', 'False']
# values = main_branch.select('count').rdd.flatMap(lambda x: x).collect()


# Create a bar chart
#plt.figure(figsize=(8, 6))
#bars = plt.bar(labels, values, color=['blue', 'green'])
#plt.xlabel('Commited to Main Branch')
#plt.ylabel('count')
#plt.yscale('log')
#plt.title('Count of Main Branch Committed')
#for bar, value in zip(bars, values):
#    height = bar.get_height()
#    plt.text(bar.get_x() + bar.get_width() / 2, height, value,
#             ha='center', va='bottom')
# Display the chart
#plt.show()

# Use Case 3 : Breakdown of events by type and number of commits per event 



In [0]:
event_type = (event_dim
              .join(event_fact['id','pe_size','pe_distinct_size'],'id', 'left' )
              .groupby('type')
              .agg(count('id').alias('NumEvents'),
                sum('pe_size').alias('NumCommits')))

In [0]:
event_type.display()
# event_type.summary().show()

type NumEvents NumCommits PullRequestReviewEvent 2500840 null PushEvent 50904451 189051065 GollumEvent 234357 null ReleaseEvent 644171 null CommitCommentEvent 506486 null CreateEvent 14718471 null PullRequestReviewCommentEvent 1438591 null IssueCommentEvent 5329569 null DeleteEvent 3623980 null IssuesEvent 2280423 null ForkEvent 1773500 null PublicEvent 308419 null MemberEvent 271739 null WatchEvent 4997435 null PullRequestEvent 9312575 null

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

# Use Case 4 : User activity should be aggregated so that a filterable chart can be populated with breakdowns of user activity by week or month. 

In [0]:
uc4_df = (event_fact
    .join(actor_dim, event_fact.actor_id == actor_dim.id)
    .join(event_dim, event_fact.event_id == event_dim.id))

In [0]:
activity_by_week_month = uc4_df.groupBy(
    actor_dim.display_login,
    # year(col("created_at")).alias("year"),
    weekofyear(col("created_at")).alias("week"),
    month(col("created_at")).alias("month")
).agg(
    count("*").alias("activity_count")
).orderBy("month", "week")

In [0]:
activity_by_week_month.createOrReplaceTempView("uc4_activity_view")

# potentially cache this?

In [0]:
def display_user_activity(username):
    query = f"""
        SELECT * FROM uc4_activity_view WHERE display_login = '{username}'
    """
    user_activity_df = spark.sql(query)
    display(user_activity_df)


In [0]:
display_user_activity("matttbe")


# Use Case 5 : Comparison of Bot vs. Human activities

In [0]:
joined_df = event_fact.join(actor_dim, event_fact.actor_id == actor_dim.id)

# Create a temporary view
joined_df.createOrReplaceTempView("activity_view")

In [0]:
def display_bot_vs_human_activity():
    query = """
    SELECT 
        is_bot,
        COUNT(*) as activity_count
    FROM 
        activity_view
    GROUP BY 
        is_bot
    """
    
    # Execute the query
    bot_human_activity_df = spark.sql(query)

    # Display the result
    display(bot_human_activity_df)


In [0]:
display_bot_vs_human_activity()